In [101]:
import gym
import numpy as np

In [102]:
import flappy_bird_gymnasium
import gymnasium as gym

# env = gym.make("FlappyBird-v0", render_mode="human", use_lidar=True)
env = gym.make("FlappyBird-v0",use_lidar=False)
obs, info = env.reset()


In [103]:
from torch import nn
import torch

In [104]:
# class PolicyNet(nn.Module):
    
#     def __init__(self,input_dim,output_dim):
#         super().__init__()
#         self.linear1 = nn.Linear(input_dim,200)
#         self.relu = nn.ReLU()
#         self.linear2 = nn.Linear(200,output_dim)
#         self.softmax = nn.Softmax(dim=-1)
    
#     def forward(self,state):
#         ### n
#         x = self.linear1(state)
#         x = self.relu(x)
#         x = self.linear2(x) # n
#         x = self.softmax(x) # n
#         return x

In [105]:
class PolicyNet(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(PolicyNet, self).__init__()
        self.network = nn.Sequential(
            nn.Linear(input_dim, 128),
            nn.ReLU(),
            nn.Linear(128, 64),
            nn.ReLU(),
            nn.Linear(64, output_dim),
            nn.Softmax(dim=-1)
        )
    
    def forward(self, x):
        return self.network(x)

In [106]:
# class ValueNet(nn.Module):
#     ### 用来学习值
    
#     def __init__(self,input_dim):
#         super().__init__()
#         self.linear1 = nn.Linear(input_dim,200)
#         self.relu = nn.ReLU()
#         self.linear2 = nn.Linear(200,1)
    
#     def forward(self,state):
#         ### n
#         x = self.linear1(state)
#         x = self.relu(x)
#         x = self.linear2(x) # n
#         return x

In [114]:
class ValueNet(nn.Module):
    def __init__(self, input_dim):
        super(ValueNet, self).__init__()
        self.network = nn.Sequential(
            nn.Linear(input_dim, 128),
            nn.ReLU(),
            nn.Linear(128, 64),
            nn.ReLU(),
            nn.Linear(64, 1)
        )
    
    def forward(self, x):
        return self.network(x)

In [115]:
from torch.distributions import Categorical
import numpy as np
np.bool8 = np.bool_

from torch.optim import AdamW

In [116]:
class Agent:
    
    def __init__(self):
        self.policy_net = PolicyNet(12,2)
        self.value_net = ValueNet(12)
        self.optimizer = AdamW(self.policy_net.parameters(),lr=1e-3)
        self.value_optimizer = AdamW(self.value_net.parameters(),lr=1e-3)
    
    def sample_action(self,state):
        probs = self.policy_net(state) # 4
        if np.random.uniform() < 0.0:
            action = np.random.randint(0,2)
            return action, torch.log(probs[action]+1e-8).detach()
        dist = Categorical(probs)
        action = dist.sample()
        log_prob = dist.log_prob(action).detach()
        return action.item(),log_prob
    
    def update(self,rewards,log_probs,xs,old_actions):
        ### 一次游戏时间
        ret = []
        adding = 0
        for r in rewards[::-1]:
            adding = adding * 0.99 + r
            ret.insert(0,adding)
        ret = torch.FloatTensor(ret)
        ret = ret - ret.mean()
        ret = ret / (ret.std()+1e-8)
        
        
        
        for _ in range(4):
            values = self.value_net(xs) ## B,48 ==> B,1
#             print(values.shape)

            new_probs = self.policy_net(xs) ## B,4
            dist = Categorical(new_probs) # B,4
#             actions = dist.sample() # B,1
            new_logprobs = dist.log_prob(old_actions.squeeze(-1)) # B,1
#             print('new log probs',new_logprobs.shape)
            advantages = ret - values.squeeze(-1).detach() # B
#             print('adv shape',advantages.shape,'ret shape',ret.shape,'value shape',values.shape,'log',log_probs.shape)
#             print('new_probs',new_probs.shape,'new_logprobs shape',new_logprobs.shape,'old_actions',old_actions.shape)
            ratio = torch.exp(new_logprobs - log_probs.squeeze(-1)) ## B
#             print('shape',ratio.shape)
            surr1 = ratio * advantages.squeeze(-1)
            surr2 = torch.clamp(ratio,0.8,1.2) * advantages
            loss = -torch.min(surr1,surr2).mean()


            self.optimizer.zero_grad()
            loss.backward()
            self.optimizer.step()


            value_loss = (values.squeeze(0) - ret).pow(2).mean()
            self.value_optimizer.zero_grad()
            value_loss.backward()
            self.value_optimizer.step()


    #         r_log_probs = []
    #         for r,log_prob in zip(ret,log_probs):
    #             r_log_probs.append(-r*log_prob)
    #         r_log_probs = torch.vstack(r_log_probs)

    #         loss = r_log_probs.sum()



            return loss

In [117]:
def convert2tensor(state):
    state_arr = torch.FloatTensor(state)
    return state_arr

In [118]:
def train(agent,env):
    success_count = []
    max_size = 1000
    for epoch in range(20000000):
        rewards = []
        xs = []
        log_probs = []
        old_actions = []
        terminated = False
        truncated = False
        success = True
        state,_ = env.reset()
        while not terminated and not truncated:
            state_arr = convert2tensor(state)
            xs.append(state_arr)
            action, log_prob = agent.sample_action(state_arr)
            next_state, reward, terminated, truncated, _ = env.step(action)
            state = next_state
            rewards.append(reward)
            log_probs.append(log_prob)
            old_actions.append(action)
        xs = torch.vstack(xs)
        log_probs = torch.vstack(log_probs)
        old_actions = torch.LongTensor(old_actions)
        loss = agent.update(rewards,log_probs,xs,old_actions) 
        success_count.append(success)
        
        
        if (epoch+1) % 10 == 0:
            print(f'epoch: {epoch}, loss: {loss}, rewards: {sum(rewards)}, count: {len(rewards)}')

In [119]:
agent = Agent()



In [ ]:
env = gym.make('FlappyBird-v0',use_lidar=False)
train(agent,env)

epoch: 9, loss: 0.04407816752791405, rewards: -6.899999999999999, count: 50
epoch: 19, loss: -0.023937908932566643, rewards: -8.099999999999998, count: 50
epoch: 29, loss: 0.013372253626585007, rewards: -8.099999999999998, count: 50
epoch: 39, loss: -0.004789469297975302, rewards: -3.899999999999998, count: 50
epoch: 49, loss: 0.00654315110296011, rewards: -7.499999999999998, count: 50
epoch: 59, loss: -0.004368507768958807, rewards: -8.099999999999998, count: 50
epoch: 69, loss: 0.0017002713866531849, rewards: -6.899999999999999, count: 50
epoch: 79, loss: -0.0033569764345884323, rewards: -7.499999999999998, count: 50
epoch: 89, loss: -0.0008155059767886996, rewards: -7.499999999999998, count: 50
epoch: 99, loss: 0.0015263987006619573, rewards: -6.899999999999999, count: 50
epoch: 109, loss: 0.00032965780701488256, rewards: -6.299999999999999, count: 50
epoch: 119, loss: -0.002542436122894287, rewards: -6.899999999999999, count: 50
epoch: 129, loss: -0.0016233313363045454, rewards: -5

epoch: 1039, loss: 0.0006546787335537374, rewards: 10.89999999999998, count: 102
epoch: 1049, loss: 0.0003180730273015797, rewards: 3.8999999999999986, count: 50
epoch: 1059, loss: 0.000244314840529114, rewards: 6.299999999999994, count: 65
epoch: 1069, loss: -0.0006813764339312911, rewards: 6.299999999999994, count: 65
epoch: 1079, loss: 0.0005248566740192473, rewards: 4.899999999999995, count: 60
epoch: 1089, loss: -2.9611587706313003e-06, rewards: 3.8999999999999986, count: 50
epoch: 1099, loss: -0.0002592706587165594, rewards: 4.1999999999999975, count: 53
epoch: 1109, loss: 0.00016945242532528937, rewards: 3.8999999999999986, count: 50
epoch: 1119, loss: 5.808320929645561e-05, rewards: 4.799999999999995, count: 59
epoch: 1129, loss: -0.00026944393175654113, rewards: 4.099999999999998, count: 52
epoch: 1139, loss: 0.00014848416321910918, rewards: 6.099999999999994, count: 63
epoch: 1149, loss: -0.00046703219413757324, rewards: 4.4999999999999964, count: 56
epoch: 1159, loss: 0.0003

epoch: 2069, loss: -9.579181642038748e-05, rewards: 3.8999999999999986, count: 50
epoch: 2079, loss: 0.000301290798233822, rewards: 4.1999999999999975, count: 53
epoch: 2089, loss: 0.0004834085702896118, rewards: 4.099999999999998, count: 52
epoch: 2099, loss: -0.00027454039081931114, rewards: 8.399999999999986, count: 86
epoch: 2109, loss: 1.8975733837578446e-05, rewards: 3.8999999999999986, count: 50
epoch: 2119, loss: -0.00033499597338959575, rewards: 3.8999999999999986, count: 50
epoch: 2129, loss: 9.423017763765529e-05, rewards: 3.8999999999999986, count: 50
epoch: 2139, loss: -1.4817377632425632e-05, rewards: 4.1999999999999975, count: 53
epoch: 2149, loss: 0.0008175015682354569, rewards: 3.8999999999999986, count: 50
epoch: 2159, loss: -8.798171620583162e-05, rewards: 6.5999999999999925, count: 68
epoch: 2169, loss: -9.927630162565038e-05, rewards: 3.8999999999999986, count: 50
epoch: 2179, loss: -4.310282747610472e-05, rewards: 4.399999999999997, count: 55
epoch: 2189, loss: -0

epoch: 3079, loss: 0.0008471186156384647, rewards: 4.1999999999999975, count: 53
epoch: 3089, loss: -0.0005863721598871052, rewards: 4.099999999999998, count: 52
epoch: 3099, loss: 0.0004789524246007204, rewards: 8.399999999999986, count: 86
epoch: 3109, loss: -0.00031126581598073244, rewards: 6.699999999999992, count: 69
epoch: 3119, loss: 0.00011244897177675739, rewards: 9.099999999999984, count: 93
epoch: 3129, loss: 0.000183765179826878, rewards: 4.399999999999997, count: 55
epoch: 3139, loss: 0.0001834249560488388, rewards: 3.8999999999999986, count: 50
epoch: 3149, loss: -5.03420815221034e-05, rewards: 6.799999999999992, count: 70
epoch: 3159, loss: -0.0004531191079877317, rewards: 4.099999999999998, count: 52
epoch: 3169, loss: -0.0004030728305224329, rewards: 3.8999999999999986, count: 50
epoch: 3179, loss: 0.0004765653284266591, rewards: 8.899999999999984, count: 91
epoch: 3189, loss: -0.0002178460854338482, rewards: 6.499999999999993, count: 67
epoch: 3199, loss: 0.0002202794

epoch: 4089, loss: -0.00036562563036568463, rewards: 3.8999999999999986, count: 50
epoch: 4099, loss: -0.0003627717378549278, rewards: 3.8999999999999986, count: 50
epoch: 4109, loss: -0.00016996980411931872, rewards: 3.8999999999999986, count: 50
epoch: 4119, loss: 9.167194366455078e-05, rewards: 4.799999999999995, count: 59
epoch: 4129, loss: 0.0002106142055708915, rewards: 3.8999999999999986, count: 50
epoch: 4139, loss: -8.28874108265154e-05, rewards: 3.8999999999999986, count: 50
epoch: 4149, loss: -8.602023444836959e-05, rewards: 3.8999999999999986, count: 50
epoch: 4159, loss: 1.9886494555976242e-05, rewards: 3.8999999999999986, count: 50
epoch: 4169, loss: -0.0001983833353733644, rewards: 3.8999999999999986, count: 50
epoch: 4179, loss: 0.00030039786361157894, rewards: 3.8999999999999986, count: 50
epoch: 4189, loss: -4.32133674621582e-05, rewards: 3.8999999999999986, count: 50
epoch: 4199, loss: -0.00022426366922445595, rewards: 3.8999999999999986, count: 50
epoch: 4209, loss:

...

epoch: 875329, loss: 0.00012905358744319528, rewards: -9.299999999999999, count: 50
epoch: 875339, loss: -7.309079228434712e-05, rewards: -9.299999999999999, count: 50
epoch: 875349, loss: -3.855705290334299e-05, rewards: -9.299999999999999, count: 50
epoch: 875359, loss: 3.6776066281163367e-06, rewards: -9.299999999999999, count: 50
epoch: 875369, loss: 1.650571903155651e-05, rewards: -9.299999999999999, count: 50
epoch: 875379, loss: 6.155967639642768e-06, rewards: -9.299999999999999, count: 50
epoch: 875389, loss: -4.951953997078817e-06, rewards: -9.299999999999999, count: 50
epoch: 875399, loss: -2.186298388551222e-06, rewards: -9.299999999999999, count: 50
epoch: 875409, loss: 2.1803380150231533e-06, rewards: -9.299999999999999, count: 50
epoch: 875419, loss: -7.534027304245683e-07, rewards: -9.299999999999999, count: 50
epoch: 875429, loss: -1.99079508433897e-07, rewards: -9.299999999999999, count: 50
epoch: 875439, loss: 3.397464638510428e-07, rewards: -9.299999999999999, count:

epoch: 876319, loss: -1.2104511370125692e-05, rewards: -9.299999999999999, count: 50
epoch: 876329, loss: -8.642673492431641e-07, rewards: -9.299999999999999, count: 50
epoch: 876339, loss: 4.507303401624085e-06, rewards: -9.299999999999999, count: 50
epoch: 876349, loss: -2.5832653136603767e-06, rewards: -9.299999999999999, count: 50
epoch: 876359, loss: 1.115798909268051e-06, rewards: -9.299999999999999, count: 50
epoch: 876369, loss: -2.837181227732799e-07, rewards: -9.299999999999999, count: 50
epoch: 876379, loss: 1.3113021779531664e-08, rewards: -9.299999999999999, count: 50
epoch: 876389, loss: -2.539158003855846e-07, rewards: -9.299999999999999, count: 50
epoch: 876399, loss: -6.67572024326546e-08, rewards: -9.299999999999999, count: 50
epoch: 876409, loss: -3.1471253691961465e-07, rewards: -9.299999999999999, count: 50
epoch: 876419, loss: -3.1232832498062635e-07, rewards: -9.299999999999999, count: 50
epoch: 876429, loss: -1.0180473282161984e-06, rewards: -9.299999999999999, 

epoch: 877309, loss: 5.4836274188119205e-08, rewards: -9.299999999999999, count: 50
epoch: 877319, loss: 6.771087441848067e-07, rewards: -9.299999999999999, count: 50
epoch: 877329, loss: -6.34193440873787e-07, rewards: -9.299999999999999, count: 50
epoch: 877339, loss: -3.194809039541724e-07, rewards: -9.299999999999999, count: 50
epoch: 877349, loss: -3.325939132992062e-07, rewards: -9.299999999999999, count: 50
epoch: 877359, loss: -1.8358230136072962e-07, rewards: -9.299999999999999, count: 50
epoch: 877369, loss: -1.497268726780021e-06, rewards: -9.299999999999999, count: 50
epoch: 877379, loss: -8.275508662336506e-06, rewards: -9.299999999999999, count: 50
epoch: 877389, loss: -6.120443140389398e-05, rewards: -9.299999999999999, count: 50
epoch: 877399, loss: -2.5534629912726814e-06, rewards: -9.299999999999999, count: 50
epoch: 877409, loss: -5.143880844116211e-05, rewards: -9.299999999999999, count: 50
epoch: 877419, loss: 1.1601448022702243e-05, rewards: -9.299999999999999, co

epoch: 878299, loss: -1.9060373233514838e-05, rewards: -9.299999999999999, count: 50
epoch: 878309, loss: 4.55260260423529e-06, rewards: -9.299999999999999, count: 50
epoch: 878319, loss: 4.961490503774257e-06, rewards: -9.299999999999999, count: 50
epoch: 878329, loss: -4.428625288710464e-06, rewards: -9.299999999999999, count: 50
epoch: 878339, loss: 1.7726421219776967e-06, rewards: -9.299999999999999, count: 50
epoch: 878349, loss: -6.139278525552072e-07, rewards: -9.299999999999999, count: 50
epoch: 878359, loss: 3.0279159091151087e-07, rewards: -9.299999999999999, count: 50
epoch: 878369, loss: -3.492832263418677e-07, rewards: -9.299999999999999, count: 50
epoch: 878379, loss: -6.139278525552072e-07, rewards: -9.299999999999999, count: 50
epoch: 878389, loss: 8.702278364580707e-08, rewards: -9.299999999999999, count: 50
epoch: 878399, loss: -6.139278525552072e-07, rewards: -9.299999999999999, count: 50
epoch: 878409, loss: -6.437301749429025e-07, rewards: -9.299999999999999, count

epoch: 879289, loss: -5.708932803827338e-06, rewards: -9.299999999999999, count: 50
epoch: 879299, loss: 4.781484676641412e-06, rewards: -9.299999999999999, count: 50
epoch: 879309, loss: -2.6428699584357673e-06, rewards: -9.299999999999999, count: 50
epoch: 879319, loss: 1.4007091522216797e-06, rewards: -9.299999999999999, count: 50
epoch: 879329, loss: -5.686283088834898e-07, rewards: -9.299999999999999, count: 50
epoch: 879339, loss: 3.8743019104003906e-07, rewards: -9.299999999999999, count: 50
epoch: 879349, loss: 3.8743019104003906e-07, rewards: -9.299999999999999, count: 50
epoch: 879359, loss: -3.492832263418677e-07, rewards: -9.299999999999999, count: 50
epoch: 879369, loss: -7.891654831837513e-07, rewards: -9.299999999999999, count: 50
epoch: 879379, loss: -1.0132789611816406e-06, rewards: -9.299999999999999, count: 50
epoch: 879389, loss: -3.7550926208496094e-06, rewards: -9.299999999999999, count: 50
epoch: 879399, loss: -2.046823465207126e-05, rewards: -9.299999999999999, 

In [ ]:
def sample_action(self,state):
    probs = self.policy_net(state) # 4
    if np.random.uniform() < 0.5:
        action = np.random.randint(0,2)
        return action, torch.log(probs[action]+1e-8).detach()
    dist = Categorical(probs)
    action = dist.sample()
    log_prob = dist.log_prob(action)
    return action.item(),log_prob.detach()

# 替换方法
import types
agent.sample_action = types.MethodType(sample_action, agent)

In [16]:
import time
def visualize_agent(env, agent, num_episodes=5):
    """
    渲染显示智能体的行动
    """
    env = gym.make('CliffWalking-v0', render_mode='human')  # 创建可视化环境
    
    for episode in range(num_episodes):
        state_tuple = env.reset()
        state = state_tuple[0] if isinstance(state_tuple, tuple) else state_tuple
        total_reward = 0
        steps = 0
        done = False
        
        print(f"\nEpisode {episode + 1}")
        
        while not done:
            env.render()  # 渲染当前状态
            
            # 将状态转换为one-hot编码
            state_onehot = np.zeros(48)
            state_onehot[state] = 1
            
            # 使用训练好的策略选择动作
            with torch.no_grad():
                if np.random.random() < 0.0:
                    action = np.random.randint(0, 4)
                else:
                    state_tensor = torch.FloatTensor(state_onehot)
                    probs = agent.policy_net(state_tensor)
                    action = probs.argmax().item()  # 使用最可能的动作
            
            # 执行动作
            step_result = env.step(action)
            if len(step_result) == 4:
                next_state, reward, done, _ = step_result
            else:
                next_state, reward, terminated, truncated, _ = step_result
                done = terminated or truncated
            
            total_reward += reward
            steps += 1
            state = next_state
            
            # 添加小延迟使动作更容易观察
            time.sleep(0.5)
        
        print(f"Episode finished after {steps} steps. Total reward: {total_reward}")
    
    env.close()

# 在主程序最后添加：
if __name__ == "__main__":    
    # 训练完成后显示智能体行动
    print("\nVisualizing trained agent behavior...")
    env = gym.make('CliffWalking-v0',render_mode='human')
    visualize_agent(env, agent)


Visualizing trained agent behavior...


2025-04-27 13:52:09.865 python[67964:170339742] +[IMKClient subclass]: chose IMKClient_Modern
2025-04-27 13:52:09.865 python[67964:170339742] +[IMKInputSession subclass]: chose IMKInputSession_Modern



Episode 1
Episode finished after 17 steps. Total reward: -17

Episode 2


KeyboardInterrupt: 

In [ ]:
env.close()